In [1]:
import pandas as pd
import numpy as np
import re
import emoji


from string import punctuation
from os import listdir
from collections import Counter
from string import punctuation
from os import listdir
from numpy import array
import tensorflow
import keras
from keras import layers
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Bidirectional, LSTM, RNN, SimpleRNN, ConvLSTM1D
from keras.layers import Flatten, Dropout
from keras.layers import Embedding, GlobalMaxPooling1D
from keras.layers.convolutional import Conv1D
from keras.layers.convolutional import MaxPooling1D


In [2]:
STOP_WORDS = set(
    """
ግን አንቺ አንተ እናንተ ያንተ ያንቺ የናንተ ራስህን ራስሽን ራሳችሁን
ሁሉ ኋላ በሰሞኑ አሉ በኋላ ሁኔታ በኩል አስታውቀዋል ሆነ በውስጥ
አስታውሰዋል ሆኑ ባጣም እስካሁን ሆኖም በተለይ አሳሰበ ሁል በተመለከተ
አሳስበዋል ላይ በተመሳሳይ አስፈላጊ ሌላ የተለያየ አስገነዘቡ ሌሎች የተለያዩ
አስገንዝበዋል ልዩ ተባለ አብራርተዋል መሆኑ ተገለጸ አስረድተዋል  ተገልጿል
ማለቱ ተጨማሪ እባክህ የሚገኝ ተከናወነ እባክሽ ማድረግ ችግር አንጻር ማን
ትናንት እስኪደርስ ነበረች እንኳ ሰሞኑን ነበሩ እንኳን ሲሆን ነበር እዚሁ ሲል
ነው እንደገለጹት አለ ና እንደተናገሩት ቢሆን ነገር እንዳስረዱት ብለዋል ነገሮች
እንደገና ብዙ ናት ወቅት ቦታ ናቸው እንዲሁም በርካታ አሁን እንጂ እስከ
ማለት የሚሆኑት ስለማናቸውም ውስጥ ይሆናሉ ሲባል ከሆነው ስለዚሁ ከአንድ
ያልሆነ ሳለ የነበረውን ከአንዳንድ በማናቸውም በሙሉ የሆነው ያሉ በእነዚሁ
ወር መሆናቸው ከሌሎች በዋና አንዲት ወይም
በላይ እንደ በማቀድ ለሌሎች በሆኑ ቢሆንም ጊዜና  ይሆኑበታል በሆነ አንዱ
ለዚህ ለሆነው ለነዚህ ከዚህ የሌላውን ሶስተኛ አንዳንድ ለማንኛውም የሆነ ከሁለት
የነገሩ ሰኣት አንደኛ እንዲሆን እንደነዚህ ማንኛውም ካልሆነ የሆኑት  ጋር ቢያንስ
ይህንንም እነደሆነ እነዚህን ይኸው  የማናቸውም
በሙሉም ይህችው በተለይም አንዱን የሚችለውን በነዚህ ከእነዚህ በሌላ
የዚሁ ከእነዚሁ ለዚሁ በሚገባ ለእያንዳንዱ የአንቀጹ ወደ ይህም ስለሆነ ወይ
ማናቸውንም ተብሎ እነዚህ መሆናቸውን የሆነችን ከአስር ሳይሆን ከዚያ የለውም
የማይበልጥ እንደሆነና እንዲሆኑ  በሚችሉ ብቻ ብሎ ከሌላ የሌላቸውን
ለሆነ በሌሎች ሁለቱንም በቀር ይህ በታች አንደሆነ በነሱ
ይህን የሌላ እንዲህ ከሆነ ያላቸው በነዚሁ በሚል የዚህ ይህንኑ
በእንደዚህ ቁጥር ማናቸውም ሆነው ባሉ በዚህ በስተቀር ሲሆንና
በዚህም መሆን ምንጊዜም እነዚህም በዚህና ያለ ስም
ሲኖር ከዚህም መሆኑን በሁኔታው የማያንስ እነዚህኑ ማንም ከነዚሁ
ያላቸውን እጅግ ሲሆኑ ለሆኑ ሊሆን  ለማናቸውም
""".split()
)

In [3]:
df = pd.read_csv("../data/new_data.csv")
df.tail()

texts   labels
50021                                          መልካም ዉይይት  neutral
50022                                        ዝናሽን ልገምግማት  neutral
50023                             ሞቶ ስዳርስ ነው ንሳ ማግባታ አብይ  neutral
50024  አብይ ሰለ ጉራጌ ተንፍስ   አብይ በጉራጌ ዞን ሚደረገዉ እነደ አልሰማ ዝ...  neutral
50025  በጉራጌ ዞን ብርሀኑ ነጋ የመረጠዉ የለም  ለምን ጠቅላይ ሚንስተር አብይ ...  neutral

In [4]:
df.labels.unique()

array(['neutral', 'positive', 'negative', '\tnegative', '\tpositive',
       'neutra', nan], dtype=object)

In [5]:
df["labels"] = df["labels"].str.strip()
df["labels"] = df["labels"].str.replace("strongPositive", "positive", regex=True)
df["labels"] = df["labels"].str.replace("\tnegative", "negative", regex=True)
df["labels"] = df["labels"].str.replace("neutra", "negative", regex=True)
df["labels"] = df["labels"].str.replace("negativel", "positive", regex=True)
df["labels"] = df["labels"].str.replace("\tneutral", "positive", regex=True)

df["labels"].unique()

array(['positive', 'negative', nan], dtype=object)

In [6]:
df.labels.value_counts()

positive    28105
negative    21915
Name: labels, dtype: int64

In [7]:
df = df.dropna()


In [8]:
df = df.drop_duplicates(subset=['texts'])
df = df.dropna(subset=["labels"])

In [9]:
labels = df["labels"].to_list()
ls = df["texts"].to_list()


In [10]:
encoded_labels = []
for label in labels:
    if label == "negative":
        encoded_labels.append(0)
    else:
        encoded_labels.append(1)

In [11]:
def remove_emojis(ls):
    new_ls = []
    for input in ls:
        new_ls.append(emoji.replace_emoji(input)
)
    return new_ls
    
def remove_punc_and_special_chars(ls): 
    new_ls = []
    for text in ls:
        text = str(text)
        normalized_text = re.sub('[\!\@\#\$\%\^\«\»\&\*\(\)\…\[\]\{\}\;\“\”\›\’\‘\"\'\:\,\.\‹\/\<\>\?\\\\|\`\´\~\-\=\+\፡\።\፤\;\፦\፥\፧\፨\፠\፣]', '',text)
        new_ls.append(normalized_text)
    return new_ls

def remove_ascii_and_numbers(ls):
    new_ls = []
    for text_input in ls:
        text_input = str(text_input)
        rm_num_and_ascii=re.sub('[A-Za-z0-9]','',text_input)
        text = re.sub('[\'\u1369-\u137C\']+','',rm_num_and_ascii)
        new_ls.append(text)
    return new_ls

def normalize_char_level_missmatch(ls):
        new_ls = []
        for input_token in ls:
            input_token = str(input_token)
            rep1=re.sub('[ሃኅኃሐሓኻ]','ሀ',input_token)
            rep2=re.sub('[ሑኁዅ]','ሁ',rep1)
            rep3=re.sub('[ኂሒኺ]','ሂ',rep2)
            rep4=re.sub('[ኌሔዄ]','ሄ',rep3)
            rep5=re.sub('[ሕኅ]','ህ',rep4)
            rep6=re.sub('[ኆሖኾ]','ሆ',rep5)
            rep7=re.sub('[ሠ]','ሰ',rep6)
            rep8=re.sub('[ሡ]','ሱ',rep7)
            rep9=re.sub('[ሢ]','ሲ',rep8)
            rep10=re.sub('[ሣ]','ሳ',rep9)
            rep11=re.sub('[ሤ]','ሴ',rep10)
            rep12=re.sub('[ሥ]','ስ',rep11)
            rep13=re.sub('[ሦ]','ሶ',rep12)
            rep14=re.sub('[ዓኣዐ]','አ',rep13)
            rep15=re.sub('[ዑ]','ኡ',rep14)
            rep16=re.sub('[ዒ]','ኢ',rep15)
            rep17=re.sub('[ዔ]','ኤ',rep16)
            rep18=re.sub('[ዕ]','እ',rep17)
            rep19=re.sub('[ዖ]','ኦ',rep18)
            rep20=re.sub('[ጸ]','ፀ',rep19)
            rep21=re.sub('[ጹ]','ፁ',rep20)
            rep22=re.sub('[ጺ]','ፂ',rep21)
            rep23=re.sub('[ጻ]','ፃ',rep22)
            rep24=re.sub('[ጼ]','ፄ',rep23)
            rep25=re.sub('[ጽ]','ፅ',rep24)
            rep26=re.sub('[ጾ]','ፆ',rep25)
            #Normalizing words with Labialized Amharic characters such as በልቱዋል or  በልቱአል to  በልቷል  
            rep27=re.sub('(ሉ[ዋአ])','ሏ',rep26)
            rep28=re.sub('(ሙ[ዋአ])','ሟ',rep27)
            rep29=re.sub('(ቱ[ዋአ])','ቷ',rep28)
            rep30=re.sub('(ሩ[ዋአ])','ሯ',rep29)
            rep31=re.sub('(ሱ[ዋአ])','ሷ',rep30)
            rep32=re.sub('(ሹ[ዋአ])','ሿ',rep31)
            rep33=re.sub('(ቁ[ዋአ])','ቋ',rep32)
            rep34=re.sub('(ቡ[ዋአ])','ቧ',rep33)
            rep35=re.sub('(ቹ[ዋአ])','ቿ',rep34)
            rep36=re.sub('(ሁ[ዋአ])','ኋ',rep35)
            rep37=re.sub('(ኑ[ዋአ])','ኗ',rep36)
            rep38=re.sub('(ኙ[ዋአ])','ኟ',rep37)
            rep39=re.sub('(ኩ[ዋአ])','ኳ',rep38)
            rep40=re.sub('(ዙ[ዋአ])','ዟ',rep39)
            rep41=re.sub('(ጉ[ዋአ])','ጓ',rep40)
            rep42=re.sub('(ደ[ዋአ])','ዷ',rep41)
            rep43=re.sub('(ጡ[ዋአ])','ጧ',rep42)
            rep44=re.sub('(ጩ[ዋአ])','ጯ',rep43)
            rep45=re.sub('(ጹ[ዋአ])','ጿ',rep44)
            rep46=re.sub('(ፉ[ዋአ])','ፏ',rep45)
            rep47=re.sub('[ቊ]','ቁ',rep46) #ቁ can be written as ቊ
            rep48=re.sub('[ኵ]','ኩ',rep47) #ኩ can be also written as ኵ  
            new_ls.append(rep48)
        return new_ls

In [12]:
def filter_stop_words(ls):
    new_ls_stop = []
    for input in ls:
        cleaned = [w for w in input.split(" ") if not w in STOP_WORDS]
        new_ls_stop.append(" ".join(cleaned).strip())

    return new_ls_stop

In [13]:
new_ls = remove_punc_and_special_chars(ls)
new_ls = remove_ascii_and_numbers(new_ls)
new_ls = remove_emojis(new_ls)
len(new_ls)

50008

In [14]:
new_ls = normalize_char_level_missmatch(new_ls)
# new_ls = [(lambda x:normalize_char_level_missmatch(x)) for x in new_ls]                  #map(normalize_char_level_missmatch, new_ls)
len(new_ls)

50008

In [15]:
new_ls

['ኢህአዴግና ኤርትራ ወይስ ኢትዮጲያና ሻእቢያ',
 'ፈጣሪ ይባርካቹ',
 'ጎሽ ተባረኩ የምታቃትሉትን ሚያገለግል ነገር ሁሉ እንዲህ ላሉ ድርጅቶች ስጡ',
 'ጥሩ ነው ግን ሌሎቹንም ተመልከቱ',
 'መሬት ጠብ እሚል ነገር አላየነም ያው ሙስናው ቀጥሏል ስራ አጡ ኑሮ ውድነቱ ተባብሶ ቀጥሏል',
 'ይገርማል  የአፀይ ቴድሮስ ልጆች ቅማንቶች በአንድ ጉድጎድ ተቀብሮ ሴገኙ ያላወገዘ አንዳችም ነገር ያለለ ስለኬንያ ሽብር ልያወግዝ ሞራል የለውም',
 'የአሰፋ ዲቃላዎችና ቅምጦች ተንጫጩ ከከከከ ምርጥ መሪ ለሀገሩ ሲተጋ ሀገር ዘራፊዎች የዘረፋው በር ሲከረቸም እያበዱ ነው አብቹ በርታልን ከጎንህ ነን  ',
 'ከውጩ ጉዞ ትንሽ ቀነስ አድርጎ ምናለበት የህወሀትን አጥፊ ግለሰቦችና ሌሎች ድርቶች ውስጥ የተወሸቁ ግለሰቦችን አድኖ ቢይዝልን መሮጥ ምን ያደርጋል',
 'ውሸታም ንፁሀንን እያሳደደ እየገደለ ነው ድል ለኦሮሞ ህዝብ',
 'አነሱ መግደል መሽነፍ ነው ማስር መሽነፍ ነው',
 'የኛ ጀግና የኦሮሚያ ፖሊስ ኢትዮጵያዊነቱን ያስመሰከረ ጀግና',
 'ዋው በጣም ምርጥ ተግባር ነው እንዲህ ነው ከህዝብ ወደ ህዝብ ማለት',
 'መሪይ ሁሉን አሳክተህ በሰላም እንድትመጣ ምኞቴ ነው እንወድሀለን',
 'በርቱ ጀግኒት',
 'ጀግኒት ',
 'የገቢዎች ሚኒስቴር  የምግብ ዘይትና ስኳር ድጋፍን ለመቄዶንያ የአረጋዉያንና የአእምሮ ህሙማን መርጃ ማእከል አደረገ',
 'አረ ሌሎችንም ምነው ጎብኛቸው ኢትዮጵያ ውስጥ ያለው መቄዶንያ ብቻ አይደለም አንድ ነገር ላይ መረባረብ ትወዳላችሁ',
 'አረ ሌሎችም እኮ አሉ የአረጋዉያን እና የአእምሮ ህሙማን መርጃ ማህከል እነሱም ጋር ጎራ እያላችሁ  የቢኒን መልካም ስራ ከማንም በላይ እወድለታለዉ እሱ የኢትዮጵያ ትልቅ ሰዉ ነዉ ቢኒዬ እግዚአብሄር እረጅም እድሜ ከጤ

In [16]:
ls

['ኢህአዴግና ኤርትራ ወይስ ኢትዮጲያና ሻዕቢያ',
 'ፈጣሪ ይባርካቹ',
 'ጎሽ ተባረኩ የምታቃትሉትን ሚያገለግል ነገር ሁሉ እንዲህ ላሉ ድርጅቶች ስጡ',
 'ጥሩ ነው ግን ሌሎቹንም ተመልከቱ',
 'መሬት ጠብ እሚል ነገር አላየነም ያው ሙሥናው ቀጥሉአል ሥራ አጡ ኑሮ ውድነቱ ተባብሶ ቀጥሉአል',
 'ይገርማል  የኣጸይ ቴድሮስ ልጆች ቅማንቶች በኣንድ ጉድጎድ ተቀብሮ ሴገኙ ያላወገዘ ኣንዳችም ነገር ያለለ ስለኬንያ ሽብር ልያወግዝ ሞራል የለውም',
 'የአሰፋ ዲቃላዎችና ቅምጦች ተንጫጩ ከከከከ ምርጥ መሪ ለሀገሩ ሲተጋ ሀገር ዘራፊዎች የዘረፋው በር ሲከረቸም እያበዱ ነው አብቹ በርታልን ከጎንህ ነን  ',
 'ከውጩ ጉዞ ትንሽ ቀነስ አድርጎ ምናለበት የህወሓትን አጥፊ ግለሰቦችና ሌሎች ድርቶች ውስጥ የተወሸቁ ግለሰቦችን አድኖ ቢይዝልን መሮጥ ምን ያደርጋል',
 'ውሸታም ንፁሃንን እያሳደደ እየገደለ ነው ድል ለኦሮሞ ህዝብ',
 'አነሱ መግደል መሽነፍ ነው ማስር መሽነፍ ነው',
 'የኛ ጀግና የኦሮሚያ ፖሊስ ኢትዮጵያዊነቱን ያስመሰከረ ጀግና',
 'ዋው በጣም ምርጥ ተግባር ነው እንዲህ ነው ከህዝብ ወደ ህዝብ ማለት',
 'መሪይ ሁሉን አሳክተህ በሰላም እንድትመጣ ምኞቴ ነው እንወድሀለን',
 'በርቱ ጀግኒት',
 'ጀግኒት ',
 'የገቢዎች ሚኒስቴር  የምግብ ዘይትና ስኳር ድጋፍን ለመቄዶንያ የአረጋዉያንና የአዕምሮ ህሙማን መርጃ ማዕከል አደረገ',
 'አረ ሌሎችንም ምነው ጎብኛቸው ኢትዮጵያ ውስጥ ያለው መቄዶንያ ብቻ አይደለም አንድ ነገር ላይ መረባረብ ትወዳላችሁ',
 'አረ ሌሎችም እኮ አሉ የአረጋዉያን እና የአዕምሮ ህሙማን መርጃ ማህከል እነሱም ጋር ጎራ እያላችሁ  የቢኒን መልካም ስራ ከማንም በላይ እወድለታለዉ እሱ የኢትዮጵያ ትልቅ ሰዉ ነዉ ቢኒዬ እግዚአብሔር እረጅም እድሜ 

In [17]:
new_ls2 = []
for text in new_ls:
    text = re.sub("[\ufeff]",'',text)
    new_ls2.append(text)
new_ls2 = filter_stop_words(new_ls2)
len(new_ls2)


50008

In [18]:
print(len(new_ls2))
print(len(list(set(new_ls2))))

50008
49319


In [23]:
# new_ls2 = set(new_ls2)
# tokens = "".join(set(new_ls2))

In [19]:
vocab2 = Counter()
for i in new_ls2:
    for j in i.split(" "):
        print(j)
        # vocab2.update(j)
print(vocab2.most_common(500))

ኢህአዴግና
ኤርትራ
ወይስ
ኢትዮጲያና
ሻእቢያ
ፈጣሪ
ይባርካቹ
ጎሽ
ተባረኩ
የምታቃትሉትን
ሚያገለግል
ላሉ
ድርጅቶች
ስጡ
ጥሩ
ሌሎቹንም
ተመልከቱ
መሬት
ጠብ
እሚል
አላየነም
ያው
ሙስናው
ቀጥሏል
ስራ
አጡ
ኑሮ
ውድነቱ
ተባብሶ
ቀጥሏል
ይገርማል

የአፀይ
ቴድሮስ
ልጆች
ቅማንቶች
በአንድ
ጉድጎድ
ተቀብሮ
ሴገኙ
ያላወገዘ
አንዳችም
ያለለ
ስለኬንያ
ሽብር
ልያወግዝ
ሞራል
የአሰፋ
ዲቃላዎችና
ቅምጦች
ተንጫጩ
ከከከከ
ምርጥ
መሪ
ለሀገሩ
ሲተጋ
ሀገር
ዘራፊዎች
የዘረፋው
በር
ሲከረቸም
እያበዱ
አብቹ
በርታልን
ከጎንህ
ነን
ከውጩ
ጉዞ
ትንሽ
ቀነስ
አድርጎ
ምናለበት
የህወሀትን
አጥፊ
ግለሰቦችና
ድርቶች
የተወሸቁ
ግለሰቦችን
አድኖ
ቢይዝልን
መሮጥ
ምን
ያደርጋል
ውሸታም
ንፁሀንን
እያሳደደ
እየገደለ
ድል
ለኦሮሞ
ህዝብ
አነሱ
መግደል
መሽነፍ
ማስር
መሽነፍ
የኛ
ጀግና
የኦሮሚያ
ፖሊስ
ኢትዮጵያዊነቱን
ያስመሰከረ
ጀግና
ዋው
በጣም
ምርጥ
ተግባር
ከህዝብ
ህዝብ
መሪይ
ሁሉን
አሳክተህ
በሰላም
እንድትመጣ
ምኞቴ
እንወድሀለን
በርቱ
ጀግኒት
ጀግኒት
የገቢዎች
ሚኒስቴር

የምግብ
ዘይትና
ስኳር
ድጋፍን
ለመቄዶንያ
የአረጋዉያንና
የአእምሮ
ህሙማን
መርጃ
ማእከል
አደረገ
አረ
ሌሎችንም
ምነው
ጎብኛቸው
ኢትዮጵያ
ያለው
መቄዶንያ
አይደለም
አንድ
መረባረብ
ትወዳላችሁ
አረ
ሌሎችም
እኮ
የአረጋዉያን
እና
የአእምሮ
ህሙማን
መርጃ
ማህከል
እነሱም
ጎራ
እያላችሁ

የቢኒን
መልካም
ስራ
ከማንም
እወድለታለዉ
እሱ
የኢትዮጵያ
ትልቅ
ሰዉ
ነዉ
ቢኒዬ
እግዚአብሄር
እረጅም
እድሜ
ከጤና
እመኝላለዉ
መቸም
የተወረሰ
የሚሆነው
እኔ
እኮ
እንደተለመደው
ሚሊየን
የሚያወጣ
እቃ
በኮንትሮባንድ
ምናምን
ሊል
ብየ
መልካም
ሁሉም
በመስመሩ
ግብር
ከፋዪ
ባገኘው
መጠን
የማያስመርር
ግብር
ከተጠየቀ
ሁሉም
ደስተኛ
ሆኖ
በሰአቱ
የሚከፍል
ይመስለኛል
ያደረጋችሁት
መልካም
እግ

In [20]:
tokenizer = Tokenizer()
# fit the tokenizer on the documents
tokenizer.fit_on_texts(new_ls)
encoded_docs = tokenizer.texts_to_sequences(new_ls)


In [21]:
len(encoded_docs)

50008

In [22]:
vocab_size = len(tokenizer.word_index) + 1

In [23]:
max_length = max([len(s.split()) for s in new_ls2])
Xtrain = pad_sequences(encoded_docs, maxlen=20, padding='post')

In [24]:
len(Xtrain)

50008

In [25]:
encoded_labels = np.array(encoded_labels)

In [26]:
len(encoded_labels)

50008

In [27]:
print(max_length)
print(vocab_size)

702
133044


In [28]:
split_frac = 0.8
train_x = Xtrain[0:int(split_frac*len(Xtrain))]
train_y = encoded_labels[0:int(split_frac*len(encoded_labels))]
remaining_x = Xtrain[int(split_frac*len(Xtrain)):]
remaining_y = encoded_labels[int(split_frac*len(encoded_labels)):]
valid_x = remaining_x[0:int(len(remaining_x)*0.5)]
valid_y = remaining_y[0:int(len(remaining_y)*0.5)]
test_x = remaining_x[int(len(remaining_x)*0.5):]
test_y = remaining_y[int(len(remaining_y)*0.5):]
print("training x rows is: " + str(len(train_x)) + " and target values len: " + str(len(train_y)))
print("validation x rows is: " + str(len(valid_x)) + " and validation values len: " + str(len(valid_y)))
print("test x rows is: " + str(len(test_x)) + " and test values len: " + str(len(test_y)))


training x rows is: 40006 and target values len: 40006
validation x rows is: 5001 and validation values len: 5001
test x rows is: 5001 and test values len: 5001


## Model 1 (CNN)

In [55]:
# define model
model = Sequential()
model.add(Embedding(vocab_size, 100, input_length=20))
model.add(Dropout(0.5))
model.add(Conv1D(filters=128, kernel_size=8, activation='relu'))
# model.add(Conv1D(filters=128, kernel_size=8, activation='relu'))
model.add(GlobalMaxPooling1D())
# model.add(Flatten())
model.add(Dense(32, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(1, activation='sigmoid'))
print(model.summary())
# compile network
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit network
model.fit(train_x, train_y, validation_data=(valid_x, valid_y), epochs=3, verbose=2)

Model: "sequential_3"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_3 (Embedding)     (None, 20, 100)           13304400  
                                                                 
 dropout_6 (Dropout)         (None, 20, 100)           0         
                                                                 
 conv1d_3 (Conv1D)           (None, 13, 128)           102528    
                                                                 
 global_max_pooling1d_3 (Glo  (None, 128)              0         
 balMaxPooling1D)                                                
                                                                 
 dense_6 (Dense)             (None, 32)                4128      
                                                                 
 dropout_7 (Dropout)         (None, 32)                0         
                                                      

In [19]:
loss, acc = model.evaluate(test_x, test_y, verbose=0)
print('Test Accuracy: %f' % (acc*100))

Test Accuracy: 66.690266


#### bidirectional lstm

In [29]:
model = Sequential()
model.add(Embedding(vocab_size, 100, input_length=20))
model.add(Dropout(0.5))
model.add(Bidirectional(LSTM(128, return_sequences=True)))
model.add(GlobalMaxPooling1D())
model.add(Dense(32, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(1, activation='sigmoid'))
print(model.summary())
# compile network
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit network
model.fit(train_x, train_y, validation_data=(valid_x, valid_y), epochs=4, verbose=2)

2023-02-23 16:55:46.666959: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2023-02-23 16:55:46.758716: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudnn.so.8'; dlerror: libcudnn.so.8: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /u01/app/oracle/product/11.2.0/xe/lib:
2023-02-23 16:55:46.758748: W tensorflow/core/common_runtime/gpu/gpu_device.cc:1850] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...
2023-02-23 16:55:46.759920: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is 

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 20, 100)           13304400  
                                                                 
 dropout (Dropout)           (None, 20, 100)           0         
                                                                 
 bidirectional (Bidirectiona  (None, 20, 256)          234496    
 l)                                                              
                                                                 
 global_max_pooling1d (Globa  (None, 256)              0         
 lMaxPooling1D)                                                  
                                                                 
 dense (Dense)               (None, 32)                8224      
                                                                 
 dropout_1 (Dropout)         (None, 32)                0

2023-02-23 16:55:48.561624: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 53217600 exceeds 10% of free system memory.
2023-02-23 16:55:48.572158: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 53217600 exceeds 10% of free system memory.


1251/1251 - 170s - loss: 0.6763 - accuracy: 0.5850 - val_loss: 0.7271 - val_accuracy: 0.3883 - 170s/epoch - 136ms/step
Epoch 2/4
1251/1251 - 172s - loss: 0.5804 - accuracy: 0.7040 - val_loss: 0.7918 - val_accuracy: 0.4821 - 172s/epoch - 137ms/step
Epoch 3/4
1251/1251 - 181s - loss: 0.3559 - accuracy: 0.8572 - val_loss: 0.9742 - val_accuracy: 0.4941 - 181s/epoch - 145ms/step
Epoch 4/4
1251/1251 - 185s - loss: 0.2230 - accuracy: 0.9175 - val_loss: 1.2531 - val_accuracy: 0.4885 - 185s/epoch - 148ms/step


In [30]:
loss, acc = model.evaluate(test_x, test_y, verbose=0)
print('Test Accuracy: %f' % (acc*100))

Test Accuracy: 52.109575


### simple RNN

In [22]:
model = Sequential()
model.add(Embedding(vocab_size, 100, input_length=20))
model.add(Dropout(0.5))
model.add(SimpleRNN(128, return_sequences=True))
model.add(GlobalMaxPooling1D())
model.add(Dense(20, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(1, activation='sigmoid'))
print(model.summary())
# compile network
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit network
model.fit(train_x, train_y, validation_data=(valid_x, valid_y), epochs=5, verbose=2)

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_2 (Embedding)     (None, 20, 100)           9038700   
                                                                 
 dropout_4 (Dropout)         (None, 20, 100)           0         
                                                                 
 simple_rnn (SimpleRNN)      (None, 20, 128)           29312     
                                                                 
 global_max_pooling1d_2 (Glo  (None, 128)              0         
 balMaxPooling1D)                                                
                                                                 
 dense_4 (Dense)             (None, 20)                2580      
                                                                 
 dropout_5 (Dropout)         (None, 20)                0         
                                                      

In [23]:
loss, acc = model.evaluate(test_x, test_y, verbose=0)
print('Test Accuracy: %f' % (acc*100))

Test Accuracy: 65.911502


#### it keeps overfitting

In [64]:
model.predict(test_x[10:20])

array([[0.9358298 ],
       [0.10251239],
       [0.64834535],
       [0.9962778 ],
       [0.03857926],
       [0.16159359],
       [0.6687596 ],
       [0.9556589 ],
       [0.989995  ],
       [0.00441548]], dtype=float32)

In [69]:
test_x[10]

array([    9,  1541, 85113,     3, 85114,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0], dtype=int32)

In [66]:
changed = tokenizer.sequences_to_texts([[9,  1541, 85113,     3, 85114,     0,     0,     0,     0,
           0,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0]])
changed

['ደስ አላቹ የቡርጅ ህዝብ ጩሉሴሶያማ']

In [41]:
def predict_sample(text, maxlen=20):
    encoded_doc = tokenizer.texts_to_sequences(text)
    test = pad_sequences(encoded_docs, maxlen, padding='post')
    prediction = model.predict(test)
    predictions = (model.predict(test) > 0.5).astype("int32")
    print('Prediction value, pre-rounding: {:.2f}'.format(prediction[0][0]))
    if predictions[0][0] == 0:
        print("Negative post detected")
    else:
        print("Negative post detected:")


In [42]:
predict_sample(["የሰላም እና የፍቅር አመት ይሁንልን"])

Prediction value, pre-rounding: 0.51
Negative post detected:


In [76]:
encoded_docs2 = tokenizer.texts_to_sequences(changed)
test = pad_sequences(encoded_docs2, maxlen=20, padding='post')
predict_x = model.predict(test)
predictions = (model.predict(test) > 0.5).astype("int32")
predictions
print(predict_x, predictions)

0

In [50]:
test_x[-1]

array([  259,   468, 90384,   181, 17551,   234, 90385,   523, 90386,
         261,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0], dtype=int32)

In [51]:
changed = tokenizer.sequences_to_texts([[259,   468, 90384,   181, 17551,   234, 90385,   523, 90386,
         261,     0,     0,     0,     0,     0,     0,     0,     0,
           0,     0]])
changed

['አስመሳይ ውሸታም በጭንቅላትህ ቆሻሻ ብታፀዳ ይሻላል ድነጋይ ራስ የምሊሊክ ዘር']

In [87]:
encoded_docs2 = tokenizer.texts_to_sequences(changed)
test = pad_sequences(encoded_docs2, maxlen=20, padding='post')
predictions = (model.predict(test) > 0.5).astype("int32")
predictions
print(predict_x, predictions)

[[0.27654654]] [[1]]


In [93]:
# model.predict("ኢትዮጲያ መጥፋት አለባቸው", batch_size=1)
encoded_docs2 = tokenizer.texts_to_sequences(["ኢትዮጲያ አያስፈልግም"])
test = pad_sequences(encoded_docs2, maxlen=20, padding='post')
predict_x = model.predict(test)
predictions = (model.predict(test) > 0.5).astype("int32")
predictions
print(predict_x, predictions)

[[0.27654654]] [[0]]


In [92]:
encoded_docs2 = tokenizer.texts_to_sequences(["የሰላም እና የፍቅር አመት ይሁንልን"])
test = pad_sequences(encoded_docs2, maxlen=20, padding='post')
predict_x = model.predict(test)
predictions = (model.predict(test) > 0.5).astype("int32")
print(predict_x, predictions)

[[0.9990956]] [[1]]


In [94]:
encoded_docs2 = tokenizer.texts_to_sequences(["ሙከራ ነው ይሄ ቢሰራ ደስ ይለኛል"])
test = pad_sequences(encoded_docs2, maxlen=20, padding='post')
predict_x = model.predict(test)
predictions = (model.predict(test) > 0.5).astype("int32")
print(predict_x, predictions)

[[0.9726012]] [[1]]


In [95]:
encoded_docs2 = tokenizer.texts_to_sequences(["ትግራይና አማራ ይገደል ይሙት"])
test = pad_sequences(encoded_docs2, maxlen=20, padding='post')
predict_x = model.predict(test)
predictions = (model.predict(test) > 0.5).astype("int32")
print(predict_x, predictions)

[[0.01092282]] [[0]]


In [96]:
encoded_docs2 = tokenizer.texts_to_sequences(["እነዝ አማራ መጥፋት አለባቸው"])
test = pad_sequences(encoded_docs2, maxlen=20, padding='post')
predict_x = model.predict(test)
predictions = (model.predict(test) > 0.5).astype("int32")
print(predict_x, predictions)

[[0.3616259]] [[0]]


In [ ]:
test = pad_sequences(encoded_docs, maxlen=20, padding='post')
model.predict(test)